# TD7 - Cryptosystème de McEliece

### 1.2. Principe du système de McEliece
La cryptographie à base de codes repose sur l’idée qu’il est difficile de décoder un code correcteur d’erreurs sans information secrète supplémentaire. Parmi ces systèmes, le cryptosystème de McEliece est un système de cryptographie asymétrique qui utilise les codes de Goppa. 

Supposons qu'Alice veuille recevoir des message de Bob de manière sécurisée. Alice choisit un code linéaire $C$ dans une famille de codes pour laquelle on possède un algorithme de décodage efficace. (dans la version originale de McEliece, on utilise un code de Goppa modifié par une permutation). Alice rend $C$ public tout en gardant l’algorithme de décodage secret. Un tel algorithme de décodage ne se limite pas à connaître $C$ au sens d’en connaître une matrice génératrice arbitraire : il nécessite de connaître les paramètres utilisés lors de la définition de $C$ dans la famille de codes choisie. Par exemple, pour des codes Goppa binaires, ces informations seraient le polynôme de Goppa et les localisateurs du code. Par conséquent, Alice peut publier une matrice génératrice de $C$ convenablement déguisée.

Plus précisément, les étapes sont les suivantes :

1. Alice choisit un code linéaire binaire $(n, k)$ $C$ capable de corriger (efficacement) $t$ erreurs, issu d’une famille de codes de grande taille (par exemple, des codes Goppa binaires). Ce choix doit permettre un algorithme de décodage efficace $A$. Soit $G$ une matrice génératrice quelconque pour $C$. Tout code linéaire possède de nombreuses matrices génératrices, mais il existe souvent un choix « naturel » pour cette famille de codes. Connaître ce choix révélerait $A$, il doit donc rester secret.

2. Alice choisit une matrice binaire non singulière aléatoire \(S\) de taille \(k \times k\).

3. Alice choisit une matrice de permutation binaire aléatoire \(P\) de taille \(n \times n\).

4. Alice calcule la matrice $k \times n$ $\hat{G} = S G P$.

5. La clé publique d’Alice est $(\hat{G}, t)$ ; sa clé privée est $(S, P, A)$.

### Chiffrement du message

Supposons que Bob souhaite envoyer un message $m$ à Alice dont la clé publique est $(\hat{G}, t)$ :

1. Bob encode le message $m$ comme une chaîne binaire de longueur $k$.
2. Bob calcule le vecteur $c' = m \hat{G}$.
3. Bob génère un vecteur binaire aléatoire $z$ de longueur $n$ contenant exactement $t$ bits à 1 (donc de poids $t$).
4. Bob envoie à Alice le texte chiffré calculé comme $c = c' + z$.

### Déchiffrement du message

À la réception de $c$, Alice effectue les étapes suivantes pour déchiffrer le message :

1. Alice calcule l’inverse de $P$ (c’est-à-dire $P^{-1}$).
2. Alice calcule $\hat{c} = c \, P^{-1}$.
3. Alice utilise l’algorithme de décodage $A$ pour décoder $\hat{c}$ et obtenir $\hat{m}$.
4. Enfin, Alice calcule $m = \hat{m} \, S^{-1}$.


# 1. Généralités sur le cryptosystème de McEliece
McEliece a originellement suggéré lui-même dans son article des paramètres de code $n=1024$, $k=524$, $t=50$. 
1) Quelle est la taille de la clé publique pour de tels paramètres ? Combien d'octets faut-il pour la stocker ? Quid de la taille du message chiffré par rapport au message en clair ? Commenter.
2) Supposons que l'on veuille décoder le message sans la clef privée. Il y a deux approches : 1) essayer de retrouver la clef privée ou 2) essayer de décoder le message sans utiliser la clef privée et uniquement $\hat G$.
a) Etudions la première approche. Retrouver la clef privée revient à retrouver $S$ et $P$. Par une approche brute-force, estimer le nombre d'essais nécessaires.
b) Pour la deuxième approche, on peut vouloir essayer de décoder un message chiffré $\hat c$ par la méthode des syndromes. Exprimer le nombre de syndromes à calculer en fonction de $n,k,t$. Faire une application numérique avec les paramètres suggérés par McEliece.

En fait, il a été prouvé par Berlekamp, McEliece et Van Tilborg que le problème de correction d'erreurs d'un code linéaire arbitraire est NP-difficile, donc il est en pratique impossible de retrouver le message $m$ uniquement à partir de $\hat G$. 

On verra plus bas des approches plus intelligentes de cryptanalyse (non brute-force).

# 2. Implémentation 
On ne va pas implémenter les codes de Goppa car cela prendrait trop de temps, mais on va les remplacer par les codes BCH que vous avez déjà vu. 
Ecrivez des fonctions python ``random_invertible(k)`` et ``random_permutation(n)`` qui génèrent des matrices inversibles et des matrices de permutation aléatoires. Récupérez aussi la fonction qui génère un code BCH à partir du TD sur les codes BCH. Utilisez-la pour fabriquer une fonction ``random_keys`` qui renvoie la paire des clefs publiques et privées (c'est à dire $G$, $S$,$P$,$\hat G$ où $G$ est une matrice génératrice du code BCH, $S$ et $P$ les matrices inversibles et de permutation aléatoires, et $\hat G = SGP$.  
On n'a pas implémenté d'algorithme de décodage de BCH efficace, donc on en restera là pour le moment.

# 3. Algorithme de Prange

On va voir une méthode de cryptanalyse du système de McEliece (ou plus généralement du décodage d'un code linéaire arbitraire dont une matrice génératrice est connue) reposant sur la notion d'*ensemble d'information*. 


Soit $C$ un code linéaire, $C \subset \mathbb F_2^n$ et $\dim C = k$. Pour $I$ un sous-ensemble de $\{1,...,n\}$ on appelle $C_I$ l'image du code par la projection sur $\mathbb F_2^I$ (on retient seulement les coordonnées qui sont dans $I$). 
On dit que $I$ de cardinal $k$ est dit un *ensemble d'information* si $C_I = \mathbb F_2^I$.

1) soit $G$ une matrice génératrice du code et $H$ une matrice de contrôle. On note $G_I$ la matrice issue de $G$ dont on n'a gardé que les colonnes dont les indices sont dans $I$. Montrer que $I$ est un ensemble d'information si et seulement si $G_I$ est inversible, si et seulement si $H_{\overline I}$ est inversible ($\overline I = \{1,...,n\} - I$).
2) Montrer qu'un code est MDS si et seulement si tout sous-ensemble $I$ de taille $k$ est un ensemble d'information. Justifier qu'un code $C$ de dimension $k$ a toujours au moins un ensemble d'information.
3) On se donne une erreur $e \in \mathbf{F}_2^n$ de poids $w$, et l’on note 
$$
s = e \, H^\top \;\in\; \mathbf{F}_2^{\,n-k}
$$
le syndrome associé.

L’idée de l’algorithme de Prange est la suivante. On choisit aléatoirement un ensemble 
d’information $I$ du code, en « pariant » que l’erreur $e \in \mathbf{F}_2^n$ est nulle sur $I$. 
Si tel est le cas, alors il existe une unique solution $x \in \mathbf{F}_2^n$ au système
$$
\begin{cases}
x_I = 0,\\[6pt]
x H^\top = s.
\end{cases}
\tag{1}
$$
Comme $e$ est aussi solution du système, on a alors $x = e$.
En pratique, pour tester si le choix de $I$ est bon, on résout le système, 
et on teste si la solution a un poids $w$. On obtient alors l'algorithme suivant.
i) Choisir aléatoirement un ensemble d'information $I$ pour le code $C$.
ii) Résoudre le système
$$\begin{cases}
x_{| I} = 0,\\
xH = s.
\end{cases}$$
iii)  Si la solution x vérifie $|x| = w$, retourner $x$. Sinon, retourner à l'étape i).



3.1) Justifier pourquoi l'algorithme de Prange termine.

 Le problème est maintenant d'estimer la *complexité moyenne* de l'algorithme de Prange. 
 
4) Fixons $n, k, q$ et $w$. Montrer que, pour $H$ et $s$ tirés uniformément, 
l'espérance du nombre de solutions $e$ du problème du syndrome (trouver $e$ tel que $e H = s$) est donnée par  
$$
\frac{\binom{n}{w}}{2^{n-k}}.
$$
 Asymptotiquement en $n$, si $\omega = w/n$ est fixé, montrer que  
$$
\frac{\binom{n}{w}}{2^{n-k}} = 2^{n h(\omega) - n + k + o(n)} = 2^{n(h(\omega) - (1 - R) + o(1))}
$$
où $R = \frac{k}{n}$ est le taux d'information du code et $h(t) =
 -\,(1 - x)\,\log_{2}(1 - x)\;-\;x\,\log_{2}(x)$ est la fonction d'entropie binaire. La formule de Stirling pourra servir.

En déduire que pour une instance aléatoire du problème du syndrome : 

1. Si $h(\omega) < 1 - R$, le nombre de solutions tend exponentiellement vers 0,
2. Si $h(\omega) > 1 - R$, le nombre de solutions est exponentiel,
3. Si $h(\omega) = 1 - R$, le nombre de solutions est polynomial en $n$.


On verra plus en détail le calcul de la complexité de l'algorithme de Prange dans le TD suivant.